In [ ]:
!conda install pymc

Solving environment: failed with initial frozen solve. Retrying with flexible solve.
Solving environment: \ ^C
failed with repodata from current_repodata.json, will retry with next repodata source.

CondaError: KeyboardInterrupt



In [ ]:
!pip install git+https://github.com/pymc-devs/pymc-bart.git

  Cloning https://github.com/pymc-devs/pymc-bart.git to /private/var/folders/44/gtm_t6x110jg6b13p4rbwkfh0000gn/T/pip-req-build-7lo1gajf
  Running command git clone --filter=blob:none -q https://github.com/pymc-devs/pymc-bart.git /private/var/folders/44/gtm_t6x110jg6b13p4rbwkfh0000gn/T/pip-req-build-7lo1gajf
  Resolved https://github.com/pymc-devs/pymc-bart.git to commit 2a8b12d7026656b25c2694e89dcf2dfbd935ae4e
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
ERROR: Could not find a version that satisfies the requirement pymc>=5.0.0 (from pymc-bart) (from versions: 2.3.5.py27-macosx-x86_64, 2.3.5.py34-macosx-x86_64, 2.3.6.py27-macosx-x86_64, 2.3.6.py34-macosx-x86_64, 2.3.6.py35-macosx-x86_64, 2.0, 2.1b0, 2.2, 2.3, 2.3.1, 2.3.2, 2.3.3, 2.3.4, 2.3.5, 2.3.6, 2.3.8, 4.0.0b1, 4.0.0b2, 4.0.0b3, 4.0.0b4, 4.0.0b5, 4.0.0b6, 4.0.0, 4.0.1, 4.1.4)
ERROR: No matching distribution found for pymc>=5.0.0
You should co

In [ ]:
from asbe.base import *
from asbe.models import *
from asbe.estimators import *
from econml.orf import DMLOrthoForest
from econml.dml import CausalForestDML
from openbt.openbt import OPENBT
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression, LogisticRegression
from sklearn.model_selection import train_test_split
from copy import deepcopy
import econml
from sklearn.gaussian_process import GaussianProcessRegressor
from sklearn.gaussian_process.kernels import ConstantKernel, RBF
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
import pickle
import scipy.linalg as la
from scipy.stats import norm
from xbart import XBART
import GPy
import pymc as pm
import pymc_bart as pmb

ModuleNotFoundError: No module named 'pymc_bart'

In [ ]:
class BARTEstimator(BaseITEEstimator):
    def fit(self, **kwargs):
        self.model_bart = pm.Model()
        X = np.concatenate((kwargs["X_training"], kwargs["t_training"].reshape((-1,1))),axis=1)            
        with self.model_bart:
            x_obs = pm.MutableData("X", X)
            self.model_bart.named_vars.pop("X")
            x_obs = pm.MutableData("X", X)
            μ = pmb.BART("μ", X=x_obs, Y=kwargs["y_training"], m=10)
            y_pred = pm.Normal("y_pred", mu=μ, observed=kwargs["y_training"],
                               shape=μ.shape)
            self.trace = pm.sample(random_seed=1005)
            
    def predict(self, **kwargs):
        X0 = np.concatenate((kwargs["X"],
                             np.zeros(kwargs["X"].shape[0]).reshape((-1,1))),axis=1)
        X1 = np.concatenate((kwargs["X"],
                             np.ones(kwargs["X"].shape[0]).reshape((-1,1))),axis=1)
        with self.model_bart:
            pm.set_data({"X": X1})
            p1 = pm.sample_posterior_predictive(self.trace)
            pm.set_data({"X": X0})
            p0 = pm.sample_posterior_predictive(self.trace)
#             ite = p1["posterior_predictive"]["y_pred"] - p0["posterior_predictive"]["y_pred"]
            p1_ypred = p1["posterior_predictive"]["y_pred"].mean(axis=0)
            p0_ypred = p0["posterior_predictive"]["y_pred"].mean(axis=0)
            ite = p1_ypred - p0_ypred
            ite = ite.mean(axis=0).to_numpy() #across chains
            if "return_mean" in kwargs:
                if kwargs["return_mean"]:
                    out =  ite.mean(axis=0)
            else:
                out =  ite.T
            if "return_counterfactuals" in kwargs:
                if kwargs["return_counterfactuals"]:
                    out = ite.mean(axis=0),p1_ypred.mean().values,p1_ypred.std().values, p0_ypred.mean().values, p0_ypred.std().values
        return out

In [ ]:
def categorical2indicator(data, name, categorical_max=4):
    '''
    Transforms categorical variable with name 'name' form a data frame to indicator variables
    
    Taken from https://github.com/IirisSundin/active-learning-for-decision-making/blob/e0c83f58181f81da2f867da4c49f1333fa7d0ae6/src/util.py#L14
    '''
    values = data[name].values
    values[values>= categorical_max] = categorical_max
    uni = np.unique(values)
    for i, value in enumerate(uni):
        data[name+'.'+str(i)] = np.array((values==value), dtype=int)
    data.drop(name, axis=1)
    return data

def preprocess(data, categorical_max=2):
    '''
    This function preprocesses the hill data 
    '''
    #Normalization is enough here
    data['bw'] = normalize(data['bw'])
    data['nnhealth'] = normalize(data['nnhealth'])
    data['preterm'] = normalize(data['preterm'])
    #Taking logarithm does not harm here before normalizing, but might be unneccessary
    data['b.head'] = normalize(np.log(data['b.head']))
    data['momage'] = normalize(np.log(data['momage']))
    
    #Categorigal variables are made to indicators, could also be just normalized:
    #Birth order is between 1
    data = categorical2indicator(data, 'birth.o', categorical_max=categorical_max)
    
    #Everything else is binary, so processing doesn't really help, makes only understanding the results harder.
    
    #For some reason, indicator variable "first" is either 1 or 2, that is why we subtract 1 from it
    data['first'] = data['first'] -1 
    
    return data

def normalize(data):
    '''
    Transforms the data to zero mean unit variance
    '''
    return (data- np.mean(data))/np.std(data)

def prepare_data(id_test, random_state, percent_for_train=0.1335):
    inputs = pd.read_csv("/Users/zoltan/Desktop/ihdp_data/inputs.csv")
    #names = ["treatment", "y_factual", "y_cfactual", "mu0", "mu1"] + [f'x{x}' for x in range(25)])
    inputs = preprocess(inputs, categorical_max=2)
    N = inputs.shape[0]
    N_train = int(np.ceil(N*percent_for_train))
    D = inputs.columns.shape[0]
    outcomes = pd.read_csv('/Users/zoltan/Desktop/ihdp_data/observed_outcomes.csv', sep=',')
    potential_outcomes = pd.read_csv('/Users/zoltan/Desktop/ihdp_data/potential_outcomes.csv', sep=',')
    potential_outcomes = potential_outcomes[['outcome_c0','outcome_c1']]
    actions = inputs['treat']
    pred_names = inputs.columns[1:D]
    predictors = inputs[pred_names]
    
    outcomes = outcomes.values
    potential_outcomes = potential_outcomes.values
    actions = actions.values
    predictors = predictors.values
    
    outcomes = np.zeros(actions.shape)
    for i in range(actions.shape[0]):
        outcomes[i] = potential_outcomes[i, actions[i]]
    
    np.random.seed(random_state)
    ind = np.arange(N)
    np.random.shuffle(ind)
    outcomes = outcomes[ind]
    potential_outcomes = potential_outcomes[ind,:]
    actions = actions[ind]
    predictors = predictors[ind,:]

    
    # Creating training data
    X_test = np.copy(predictors[id_test,:])
    y_test = np.copy(outcomes[id_test])
    t_test = np.copy(actions[id_test])
    ite_test = potential_outcomes[id_test, 1]  - potential_outcomes[id_test, 0]
                     
    #shuffle the rest again (not test sample)
    np.random.seed(random_state)
    
    ind = np.arange(N-1)
    np.random.shuffle(ind)
    outcomes = outcomes[np.arange(N)!=id_test][ind]
    potential_outcomes = potential_outcomes[np.arange(N)!=id_test][ind,:]
    actions = actions[np.arange(N)!=id_test][ind]
    predictors = predictors[np.arange(N)!=id_test,:][ind,:]  
                     
    X_train, y_train, t_train = predictors[:N_train,:], outcomes[:N_train], actions[:N_train]
    y0_train, y1_train = potential_outcomes[:N_train, 0], potential_outcomes[:N_train, 1]
    ite_train = y1_train - y0_train
                     
    X_pool, y_pool, t_pool = predictors[N_train:,:], outcomes[N_train:], actions[N_train:]
    y0_pool, y1_pool = potential_outcomes[N_train:, 0], potential_outcomes[N_train:, 1]
    ite_pool = y1_pool - y0_pool
            
#     for col in ['bw','nnhealth', 'preterm', 'b.head','momage']:
#         scalers[col] = StandardScaler()
#         X_train[col] = scalers[col].fit_transform(X_train[col].to_numpy().reshape(-1,1))
#         X_pool[col] = scalers[col].transform(X_pool[col].to_numpy().reshape(-1,1))
#         try:
#             X_test[col] = scalers[col].transform(X_test[col].to_numpy().reshape(-1,1))
#         except:
#             X_test[col] = scalers[col].transform(X_test[col].reshape(-1,1))
    #X_train, X_pool, y_train, y_pool = X[], X_pool, y_train, y_pool
    ds = {"X_training": X_train,
     "y_training": y_train,
     "t_training": t_train,
     "ite_training": ite_train,
     "X_pool": X_pool, 
     "y_pool": y_pool,
     "t_pool": t_pool,
     "y1_pool": y1_pool,
     "y0_pool": y0_pool,
     "ite_pool": ite_pool,
     "X_test": X_test.reshape((1,-1)),
     "y_test": y_test,
     "t_test": t_test,
     "ite_test": ite_test.reshape((-1,1))
     }
    return ds

In [ ]:
class GPyEstimator(BaseITEEstimator):
    # https://github.com/IirisSundin/active-learning-for-decision-making/blob/master/src/gpmodel.py
    def __init__(self,**kwds):
        super().__init__(**kwds)
        self.name = "gpy"
        self.update = False
    
    def _create_model(self, x, y):
        d = x.shape[1]
        prior = GPy.core.parameterization.priors.Gamma(a=1.5,b=3.0)
        kern = GPy.kern.RBF(input_dim=d, ARD=True)
        kern.variance.set_prior(prior, warning=False)
        kern.lengthscale.set_prior(prior, warning=False)
        lik1 = GPy.likelihoods.Gaussian()
        lik1.variance.set_prior(prior, warning=False)
        lik_expert = GPy.likelihoods.Gaussian()
        lik_expert.variance.set_prior(prior, warning=False)
        lik = GPy.likelihoods.MixedNoise([lik1, lik_expert])
        output_index = np.ones(x.shape[0])
        model = GPy.core.GP(X =  x,
                                 Y =  y.reshape(-1, 1), 
                                 kernel=kern,
                                 likelihood=lik, 
                                 Y_metadata = {'output_index':output_index})
        model.optimize()
        return model
        
    def fit(self, **kwargs):
        if self.update:
            action = "t" if kwargs["t_training"] == 1 else "c"
            predictor = kwargs["X_training"]
            oracle_outcome = kwargs["y_training"]
            mcopy = {}
            mcopy["c"] = deepcopy(self.models["c"])
            mcopy["t"] = deepcopy(self.models["t"])
            mcopy[action].Y_metadata['output_index'] = np.r_[mcopy[action].Y_metadata['output_index'], np.array([1])]
            mcopy[action].set_XY(np.r_[mcopy[action].X, predictor], np.r_[mcopy[action].Y, oracle_outcome], )
            mcopy[action].optimize()
            self.updated_model = mcopy
        else:
            self.models = {}
            Xt, yt = kwargs["X_training"][(kwargs["t_training"] == 1), :],\
                    kwargs["y_training"][(kwargs["t_training"] == 1)]
            Xc, yc = kwargs["X_training"][(kwargs["t_training"] == 0), :],\
            kwargs["y_training"][(kwargs["t_training"] == 0)]
            self.models["c"] = self._create_model(Xc, yc)
            self.models["t"] = self._create_model(Xt, yt)
        
    def predict(self, X, **kwargs):
        if len(X.shape) == 1:
            X = X.reshape((1, -1))
        p1 = self.models["t"].posterior_samples_f(X, 100)
        p0 = self.models["c"].posterior_samples_f(X, 100)
        ite = p1 - p0
        ite = ite.squeeze(1)
        if "return_mean" in kwargs:
            if kwargs["return_mean"]:
                ite = self.models["t"].predict_noiseless(X)[
                    0] - self.models["c"].predict_noiseless(X)[0]
        if "return_counterfactuals" in kwargs:
            if kwargs["return_counterfactuals"]:
                p1, p1s = self.models["t"]._raw_predict(X)
                p0, p0s = self.models["c"]._raw_predict(X)
                ite = (ite, p1, p0, p1s, p0s)
        return ite

In [ ]:
class ExpectedReliability(BaseAcquisitionFunction): #'decerr'
        '''
        Uses Gauss-Hermite quadrature to compute expected type S error rate
        '''
        def error_rate(self, preds):
            mu_tau = np.mean(preds[0])
            sd_tau = np.std(preds[0])
            alpha = norm.cdf(-np.abs(mu_tau)/sd_tau)
            return alpha
        
        def calculate_metrics(self, model, dataset):
            utilities = np.zeros(dataset["X_pool"].shape[0])
            reload = False
            for n in range(dataset["X_pool"].shape[0]):
                x_star = dataset["X_pool"][n,:].reshape(1,-1)
                a_star = 1 - dataset["t_pool"][n] # counterfactual action
                decerr = 0.0
                points, weights = np.polynomial.hermite.hermgauss(16) 
                for ii, yy in enumerate(points):
                    preds_star = model.predict(X=x_star, return_counterfactuals=True)
                    if a_star == 1:
                        mu_star, S_star = preds_star[1], preds_star[3]
                    else:
                        mu_star, S_star = preds_star[2], preds_star[4]
                    y_star = np.sqrt(2)*np.sqrt(S_star)*yy + mu_star #for substitution
                    new_data = {"X_training": np.concatenate((dataset["X_training"], x_star)),
                               "y_training":  np.concatenate((dataset["y_training"], 
                                                              y_star.reshape((1,)))),
                                "t_training": np.concatenate((dataset["t_training"], 
                                                              a_star.reshape((1,))))
                               }
                    if model.name == "gpy":
                        model.update = True
                        model.fit(X_training=x_star,
                                        y_training=y_star,
                                        t_training=a_star.reshape((1,)))
                        gpy_new = GPyEstimator()
                        gpy_new.models = model.updated_model
                        preds_next = gpy_new.predict(X = dataset["X_test"],
                                         return_counterfactuals=True)
                        model.update = False
                    else:
                        try:
                            new_model = deepcopy(model)
                            new_model.fit(**new_data)
                            preds_next = new_model.predict(X = dataset["X_test"],
                                         return_counterfactuals=True)
                        except TypeError:
                            nm = XBARTEstimator(model = XBART(num_sweeps=20), two_model = False)
                            nm.fit(**new_data)
                            preds_next = nm.predict(X = dataset["X_test"],
                                         return_counterfactuals=True)
                    util = 1-self.error_rate(preds_next)
                    decerr += weights[ii] * 1/np.sqrt(np.pi) * util
                utilities[n] = decerr
                print(f"{n} is done")
            return decerr


In [ ]:
# class ExpectedTargetedIG(BaseAcquisitionFunction):
#     def mvn_KL(self, mu1, S1, mu2, S2):
#         '''
#         KL divergence between two multivariate normals
#         '''
#         if type(mu1)!=np.ndarray:
#             d = 1
#         else:
#             d = mu1.shape[0]
#         KL = 0.5*(np.log(la.det(S2)/la.det(S1)) + np.trace(la.inv(S2).dot(S1)) + (mu1 - mu2).T.dot(la.inv(S2).dot((mu1 - mu2))) - d)
#         return KL
    
#     def calculate_metrics(self, model, dataset):
#         '''
#         Uses Gauss-Hermite quadrature to compute expected information gain in decision
#         '''
#         ite_pred, p1, p0, p1s, p0s = model.predict(X = dataset["X_test"],
#                                          return_counterfactuals=True)
#         ypred = np.where(p1 > p0, p1, p0)
#         Spred = np.where(p1 > p0, p1s, p0s)
#         N = dataset["X_pool"].shape[0]
#         # d = self._decide(preds)
#         # ypred, Spred = preds[d]
#         X_STAR = dataset["X_pool"]
#         # x_star = self.dat['predictors'][n,:].reshape(1,-1)
#         a_star = 1 - dataset["t_pool"] # counterfactual action

#         points, weights = np.polynomial.hermite.hermgauss(32) 
#         scores = []
#         NUM_SIMULATIONS = 10
#         sims = np.random.choice(N, NUM_SIMULATIONS, replace=False)
#         for i in sims:
#             x_star = X_STAR[i, :].reshape((1, -1))
#             preds_star = model.predict(x_star, return_counterfactuals=True)
#             targig = 0.0
#             for ii, yy in enumerate(points):
#                 if dataset["t_pool"][i] == 1:
#                     mu_star, S_star = preds_star[1], preds_star[3]
#                 else:
#                     mu_star, S_star = preds_star[2], preds_star[4]
#                 y_star = np.sqrt(2)*np.sqrt(S_star)*yy + mu_star #for substitution
#                 #try:
#                 new_model = deepcopy(model)
#                 new_data = {"X_training": np.concatenate((dataset["X_training"], x_star)),
#                            "y_training":  np.concatenate((dataset["y_training"], 
#                                                           dataset["y_pool"][i].reshape((1,)))),
#                             "t_training": np.concatenate((dataset["t_training"], 
#                                                           dataset["t_pool"][i].reshape((1,))))
#                            }
#                 new_model.fit(**new_data)
#                 preds_next = new_model.predict(X = dataset["X_test"],
#                                  return_counterfactuals=True)
#                 #model_star = self.update(a_star, x_star, y_star)
#                 # preds_next = self.predict(new_predictors, model_star)
#                 #    preds_next = self.predict(new_predictors)
#                 D_KL = 0
#                 for d in range(2):
#                     ypred_next, Spred_next = preds_next[d+1], preds_next[d+3]
#                     D_KL += self.mvn_KL(ypred_next, Spred_next, ypred, Spred)
#                 targig += weights[ii] * 1/np.sqrt(np.pi) * D_KL
#             scores += [targig]
#         scs = np.zeros(N)
#         scs[sims] = np.array(scores).ravel()
#         return scs

In [ ]:

class XBARTEstimator(BaseITEEstimator):
    def __init__(self, model, two_model=False):
        super().__init__(model = model, two_model = two_model,dataset=None, ps_model=None)
        
    def predict(self, **kwargs):
        X0 = np.concatenate((kwargs["X"],
                             np.zeros(kwargs["X"].shape[0]).reshape((-1,1))),axis=1)
        X1 = np.concatenate((kwargs["X"],
                             np.ones(kwargs["X"].shape[0]).reshape((-1,1))),axis=1)
        if "return_mean" in kwargs:
            if kwargs["return_mean"] is True:
                out = self.model.predict(X1) - self.model.predict(X0)
        else:
            out = self.model.predict(X1, return_mean=False) - self.model.predict(X0, return_mean=False)
        if "return_counterfactuals" in kwargs:
            if kwargs["return_counterfactuals"] is True:
                p1 = self.model.predict(X1, return_mean=False)
                p0 = self.model.predict(X0, return_mean=False)
                return (out, np.mean(p1), np.mean(p0), np.std(p1), np.std(p0))
        return out
        


In [ ]:
ests = {#"gpy":GPyEstimator()
#         "gpy":GPyEstimator(),
#          "openbt": OPENBTITEEstimator(model=openbt.OPENBT(model="bart"),two_model=True),
#          "bart":BARTEstimator(),
         "xbart_optimized":XBARTEstimator(model=XBART( num_sweeps= 50,
                                            num_trees=400,
                                            beta=3,alpha=0.6))
}
ests

{'xbart_optimized': XBARTEstimator(model=XBART(num_trees = 400, num_sweeps = 50, n_min = 1, num_cutpoints = 100, alpha = 0.6, beta = 3.0, tau = 'auto', burnin = 15, mtry = 'auto', max_depth_num = 250, kap = 16.0, s = 4.0, verbose = False, parallel = False, seed = 0, model_num = 0, no_split_penality = 'auto', sample_weights_flag = True, num_classes = 1))}

In [ ]:
model_results = {}
for key, value in ests.items():
    res = {}
    for i in range(1):
        for d in range(747):
            ds = prepare_data(d, i)
            asl = BaseActiveLearner(estimator = value,
                                     acquisition_function=[RandomAcquisitionFunction(name="random",
                                                                                     method = "top" ),
                                                           EMCMAcquisitionFunction(name="emcm",
                                                                                   method = "top"), 
                                                           UncertaintyAcquisitionFunction(name="unc"),
#                                                            ExpectedReliability(name="er", method="top")
                                                         ],
                                    assignment_function=BaseAssignmentFunction(),
                                    stopping_function = None,
                                    dataset=ds,
                                    al_steps=6)
            _ = asl.simulate(no_query=1, metric=["PEHE", "decision"])
            res[f"{key}_{i}_{d}"] =  pd.DataFrame(asl.simulation_results)
            res[f"{key}_{i}_{d}"]["sim"] = i
            res[f"{key}_{i}_{d}"]["data"] = d
#             with open(f"/Users/zoltan/Desktop/{key}_res.pickle", "wb") as output_file:
#                 pickle.dump(res, output_file)
#             print(res)
#             print(f"D {d} is done")
#             temp_df = create_table(res)
#             temp_df.to_csv("/Users/zoltan/Desktop/asbe_ihdp_results_xbart.csv")

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0}
{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1}
{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                           

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

...

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

{'xbart_optimized_0_0':                                                    random_1  sim  data
PEHE      {1: 8.758554388132762, 2: 8.780557046730337, 3...    0     0
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     0, 'xbart_optimized_0_1':                                                    random_1  sim  data
PEHE      {1: 3.723845101843498, 2: 3.745831708312638, 3...    0     1
decision   {1: 1.0, 2: 0.0, 3: 1.0, 4: 0.0, 5: 0.0, 6: 0.0}    0     1, 'xbart_optimized_0_2':                                                    random_1  sim  data
PEHE      {1: 5.474600543858589, 2: 5.458972230940921, 3...    0     2
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     2, 'xbart_optimized_0_3':                                                    random_1  sim  data
PEHE      {1: 0.8395753726799473, 2: 0.8239665107499228,...    0     3
decision   {1: 0.0, 2: 1.0, 3: 1.0, 4: 1.0, 5: 0.0, 6: 0.0}    0     3, 'xbart_optimized_0_4':                             

In [ ]:
def _normalize(df, col):
    return pd.json_normalize(df.loc[:, f"{col}_1"]).rename({i:f"{col}_step_{i}" for i in range(7)},
                                                      axis=1)

def create_table(res, metric="PEHE"):
    concated = pd.concat([x for x in res.values()])
    concated = concated.loc[metric]
    df_all = pd.concat(
        [_normalize(concated, "random"),
        _normalize(concated, "emcm"),
        _normalize(concated, "unc"),
        _normalize(concated, "er"),
        concated[["sim", "data"]].reset_index(drop=True)], axis = 1)
    df_all["random_change"] = df_all["random_step_1"] - df_all["random_step_6"]
    df_all["emcm_change"] = df_all["emcm_step_1"] - df_all["emcm_step_6"]
    df_all["unc_change"] = df_all["unc_step_1"] - df_all["unc_step_6"]
    df_all["er_change"] = df_all["er_step_1"] - df_all["er_step_6"]
    return df_all

In [ ]:
df_all = create_table(res)

In [ ]:
df_all

random_step_1  random_step_2  random_step_3  random_step_4  random_step_5  \
0       8.880938       8.890996       8.853116       8.844894       8.904100   
1       3.914546       3.860475       3.822083       3.852133       3.943620   
2       5.511446       5.668999       5.475003       5.539919       5.549853   
3       0.877771       1.015919       0.836278       0.916644       0.911129   
4       0.115128       0.292169       0.073635       0.175088       0.123065   

   random_step_6  emcm_step_1  emcm_step_2  emcm_step_3  emcm_step_4  ...  \
0       8.811424     8.880938     8.943996     8.750183     8.701281  ...   
1       3.749517     3.914546     3.907945     3.747897     3.758379  ...   
2       5.616661     5.511446     5.570250     5.564982     5.594148  ...   
3       0.995237     0.877771     0.936282     0.926257     0.955423  ...   
4       0.215027     0.115128     0.210925     0.203962     0.192780  ...   

   er_step_3  er_step_4  er_step_5  er_step_6  sim  data  random_change  \
0   8.898786   8.861937   8.797540   8.807472    0     0       0.069514   
1   3.846603   3.841194   3.827086   3.835575    0     1       0.165028   
2   5.487791   5.382646   5.580682   5.550329    0     2      -0.105215   
3   0.837369   0.729161   0.912283   0.901891    0     3      -0.117466   
4   0.112476   0.008239   0.125856   0.124766    0     4      -0.099899   

   emcm_change  unc_change  er_change  
0     0.038792    0.097124   0.073466  
1     0.065629    0.081235   0.078971  
2    -0.006887    0.009243  -0.038883  
3    -0.001837    0.029150  -0.024120  
4    -0.001837    0.029150  -0.009638  

[5 rows x 30 columns]

In [ ]:
df_all[["random_step_1"]].mean()

random_step_1    12.497202
dtype: float64

In [ ]:
df_all[["random_step_1", "emcm_step_1", "unc_step_1", "er_step_1"]].mean()

random_step_1    3.859966
emcm_step_1      3.859966
unc_step_1       3.859966
er_step_1        3.859966
dtype: float64

In [ ]:
df_all[["random_step_6", "emcm_step_6", "unc_step_6", "er_step_6"]].mean()

random_step_6    3.877573
emcm_step_6      3.841194
unc_step_6       3.810786
er_step_6        3.844007
dtype: float64

In [ ]:
with open("/Users/zoltan/Desktop/xbart_res.pickle", "wb") as output_file:
    pickle.dump(res, output_file)